# Choropleth maps

files needed = ('ne_50m_admin_0_counties', 'cb_2021_us_county_5m.shp', 'results.csv')

We have figured out how to plot geographic data using geopandas. We needed shape files loaded into geoDataFrames with one column assigned as the geoDataFrame's geometry. Once that is set up, plotting is easy. 

In this notebook we are going to learn how to assign colors to maps based on a variable &mdash; a *choropleth*. We looked at an example of this kind of figure on the first day of class: [Voting patterns in Wisconsin](https://www.cnn.com/election/2020/results/state/wisconsin/president). By the end of this workbook, we will have made a similar map. 

In [ ]:
import pandas as pd                         # pandas for data management
import geopandas                            # geopandas for maps work
import matplotlib.pyplot as plt             # matplotlib for plotting details

## Choropleth maps

A choropleth map is one with regions assigned colors based on a variable. 
* 'column' is the column name that holds the variable to color by
* 'cmap' is the color scheme. There are [many](https://matplotlib.org/stable/tutorials/colors/colormaps.html). Review the vizualization notebook for a refresher on what types of color map are appropriate for different applications.  

Let's return to the world map from the *maps* notebook.  

In [ ]:
# Load the shape file
world = geopandas.read_file('ne_50m_admin_0_countries.zip')
world.head(2)

The dataset includes measures of population and GDP. Let's create a map where the color of each country depends on GDP per capita. 

In [ ]:
world['gdp_cap'] = world['GDP_MD']/world['POP_EST']
world['gdp_cap'].describe()

In [ ]:
world[world['NAME']=='United States of America'][['NAME','gdp_cap','GDP_MD','POP_EST']]

These numbers don't make much sense. There must be a scaling issue. This is why we always do sanity checks. Do the data look like we expect?

The GDP data are in millions (US GDP is on the order of trillions). The population data are not adjusted. (US population is around 330 million).

In [ ]:
world['gdp_cap'] = world['GDP_MD']/world['POP_EST']*1000000
print('US GDP per capita is {0:,.0f}'.format(float(world[world['NAME']=='United States of America']['gdp_cap'])))

That looks better. Let's check it out once more. 

In [ ]:
world = world.sort_values('gdp_cap', ascending=False)
world.loc[:, ['NAME', 'gdp_cap']]

The data for small places is crazy. Antarctica's GDP per capita doesn't really make sense. Let's only plot countries with populations greater than 50,000. I'm sorry to do this to you, Falkland Islands. 

In [ ]:
world[world['POP_EST']<50000].head(10)

Time to create the choropleth. The only difference from plotting a "regular" map is that we use the `cmap` option instead of the `color` option. For this example, I will use the [Blues](https://matplotlib.org/stable/tutorials/colors/colormaps.html#sequential) colormap. 

In [ ]:
fig, gax = plt.subplots(figsize=(15,5))

world[world['POP_EST']>50000].plot(ax = gax, column='gdp_cap', edgecolor='black', cmap = 'Blues', legend=True)

plt.axis('off')

plt.show()

That legend is atrocious. Never trust the defaults. 

The legend is taking up the entire vertical span of the figure, which I sized at (15,10), even though the map does not. There are two ways to fix this. 

1. Shrink the vertical size. (15,5) starts to look pretty good. 

2. Add a separate legend to our plot. This will require digging into the guts of matplotlib. It's a good thing we are already experienced with matplotlib.  First, we add a separate axis to our plot. Then we will tell the geopandas plot command to add the legend to the new axis. \[This method works on other types of plots as well. It is sometimes useful for heat maps and creating insets.\]

Let's take a look at the second way. It will teach us a bit more about axes, which will come in handy if we ever want to make map insets. 

In [ ]:
# import the make_axes_locatable method from matplotlib
from mpl_toolkits.axes_grid1 import make_axes_locatable

In [ ]:
fig, map_ax = plt.subplots(figsize=(15,10))

# Adapted from https://geopandas.org/en/stable/docs/user_guide/mapping.html

# Create an axis divider object. It allows us to add another axis to the current one (map_ax).
divider = make_axes_locatable(map_ax)

# Add a second axis to the right of the original axes. 
# Make the new axes 3% of the original and add some padding between them.
legend_ax = divider.append_axes('right', size='3%', pad=0.1)


# The plot command works like normal, but: we plot the map on the map_ax (using the ax option)
# and we plot the legend on the legend_ax (using the cax option).
world[world['POP_EST']>50000].plot(
                                   ax = map_ax,                          # give ax the axes for the map
                                   column='gdp_cap',                     # the quantitative column
                                   edgecolor='black',                    # set the edge color
                                   cmap = 'Reds',                        # set the color map
                                   legend=True, cax=legend_ax)           # give cax the legend axes
                                   
                                                
# Here I ony turn off the axis of the main plot
map_ax.axis('off')

plt.show()

You can experiment with different padding, widths, locations, and color maps. 

## Practice

At the end of the *maps* notebook we created a map of Wisconsin's counties. We learned not only how to plot shape files, but where to find the shape files. 

Now let's color the map to reflect voting patterns in the 2020 presidential election. 

The steps:

1. Plot the county borders
3. Merge data on votes with geographical data
4. Color the map

We have already figured out the first step. The code below reproduces the map we finished with in the *maps* notebook. 

### 1. Plot the county borders


To read the data
```python
# Read in the counties shape file.
counties = geopandas.read_file('cb_2021_us_county_5m.zip')

# WI fips code is 55. Keep just the WI counties.
wi_counties = counties[counties['STATEFP']=='55'].copy()
wi_counties.head(2)
```

To make the plot
```python
fig, gax = plt.subplots(figsize=(10,10))
wi_counties.plot(ax=gax, edgecolor='black', color = 'white')
plt.axis('off')
plt.show()
```


### 2. Get the vote totals and merge them 

Time to add the voter totals. I downloaded the results from the [Wisconsin Elections Commission website](https://elections.wi.gov/elections/election-results/results-all#accordion-868). The file is 'County by County Report all offices.xlsx'. Go ahead and open up the file. It's a mess! 

I saved a cleaned-up version of the file to 'results.csv' which we can use to save the hassle with cleaning the data. For fun, you should load the raw data and try beating it into shape. That's what you normally would have to do...and, it's fun.

**2(a).**  Load 'results.csv' to a DataFrame named `results`. Note, this is not a GeoDataFrame, this data doesn't have a geometery to it, it just has county names and vote counts.

**Check your dtypes!**

We need to standardize the county names to that we can merge the vote totals with the county shapefile. Let's make the county names 'title case'. We should also remove any extra whitespace. We know how to fix this up. 

**2(b).** Convert the county names in `results` to title case. Strip any leading/trailing whitespace in the county names.

**2(c).** Convert the county names in `wi_counties` to title case. Strip any leading/trailing whitespace in the county names.

**2(d).** Merge `wi_counties` and `results`. Use the indicator option in the merge, and check that everything matched up using `.value_counts()`. There are 72 counties in Wisconsin.

**2(e).** Create a variable called 'trump_share' that is the share of trump votes out of the total vote count.

### 4. Color the map

Create a chloropeth map with colors that correspond to Trump's share of the vote. 

Remember the extra arguments.

1. `column` is set to the column name of the data we want to be 'colored'
2. `cmap` determines the color scheme. Try 'Reds' or 'bwr' or 'seismic'.
3. `legend` turn on the legend

If you use a *diverging color map*, like 'bwr,' you might want to specify the [min and max values](https://geopandas.org/en/stable/docs/reference/api/geopandas.GeoDataFrame.plot.html) for the legend. (Why?) 

4. Try changing the edge color of the counties to white. 
5. Add a title to your legend. Use the ` legend_kwds={'label': 'Legend title text'}` option of the plot command. ([docs](https://geopandas.org/en/stable/docs/user_guide/mapping.html#creating-a-legend)).

## Finish early?

1. Use the 'cities_4269' file on the course website and add Kenosha, Green Bay, Madison, and Milwaukee to your map. Try a white color and a black outline for the circle. Experiment with different combinations of colors and edge colors. What works best?
2. Label the cities. 

## Even more!

The labels on the map on [cnn](https://www.cnn.com/election/2020/results/state/wisconsin/president) have a white "shadow" around them. It's not too hard to add this to our labels. This technique works for any matplotlib text (and other objects, too). See this documentation for [path effects](https://matplotlib.org/stable/users/explain/artists/patheffects_guide.html#path-effects-guide) if you are interested in learning more.

1. Start by importing the patheffects module from matplotlib. This gives us some more tools. 

```python
import matplotlib.patheffects as PathEffects
```

2. The patheffects option in `.annotate()` takes a list of values. Try this: 

```python
.annotate(label, xy=(x,y), xytext=(3,3), textcoords='offset points',  
          path_effects=[PathEffects.withStroke(linewidth=3, foreground='white')]
          )
```
    Experiment with different line widths, colors...